Team Comparisons

In [10]:
import csv
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression

Import Data

In [11]:
Stats = []
with open('TI9.csv', newline = '') as csvfile:
    spamreader = csv.reader(csvfile, delimiter = ',', quotechar='|')
    for row in spamreader:
        Stats.append(row)

Games Array

In [12]:
Team1 = []
Team2 = []
Winner = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        Team1.append(Stats[i][1])
        Team2.append(Stats[i][4])
        Winner.append(Stats[i][7])
        i += 1       

Total Wins per team

In [13]:
Teamlist = ['OG','Team Liquid', 'PSG.LGD','Team Secret','Vici Gaming','Evil Geniuses','Royal Never Give Up','Infamous Gaming', 'Newbee', 'TNC Predator','Virtus.pro','Fnatic','Alliance','Mineski','Natus Vincere', 'Chaos Esports Club', 'KEEN GAMING', 'Ninjas in Pyjamas']


wij = np.zeros((len(Teamlist), len(Teamlist)))


wincounts = []
for x in Teamlist:
    wincounts.append(Winner.count(x))

Wins i vs j matrix

In [14]:
binWins = np.zeros(len(Winner))
for i in range(len(Winner)):
    if Winner[i] == Team1[i]:
        binWins[i] = 1

d = {'Radiant':Team1, 'Dire':Team2, 'Winner':binWins}

index_dict = {'OG':0,'Team Liquid':1,'PSG.LGD':2,'Team Secret':3,'Vici Gaming':4,'Evil Geniuses':5,'Royal Never Give Up':6,'Infamous Gaming':7,'Newbee':8,'TNC Predator':9,'Virtus.pro':10,'Fnatic':11,'Alliance':12,'Mineski':13,'Natus Vincere':14,'Chaos Esports Club':15,'KEEN GAMING':16,'Ninjas in Pyjamas':17}

games = pd.DataFrame(data = d)

Wi = pd.DataFrame(np.array([wincounts]), columns = Teamlist)
    
np.array(wincounts)


for n in range(len(games.loc[:,'Radiant'])):
    i = games.loc[n,'Radiant']
    j = games.loc[n,'Dire']
    if games.loc[n,'Winner'] == i:
        wij[index_dict[i],index_dict[j]] += 1
    else:
        wij[index_dict[j],index_dict[i]] += 1

To implement the Bradley Terry Model as a GLM we will be relying on the logistic model for binomially distributed data as implemented by Jamil, 2010 such that logit(p_(i>j))= log(p_(i>j)/(1-p_(i>j)) = lamda_i - lambda_j


Model Matrix

From here we should be able to apply the logit model as we have pij, X and unknowns lambda where
logit[pij] = X*Lambda

Our inputs are clearly 2 teams with an output vector as 0 or 1 depending whether team 1 or team 2 wins

Lets do some quick Data fixing on our existing design and response matrixes

In [15]:
"""Number of teams"""
k = len(Teamlist)
N = len(Winner)
X = np.zeros((N,k))


def designMatrix(data, index_dict):
    """ Creates a design matrix for standard Bradley Terry Model"""
    N = len(data.index)
    k = len(index_dict.keys())
    X = np.zeros((N,k))
    gameNumber = 0
    for index, row in data.iterrows():
        X[gameNumber][index_dict[row[0]]] = 1
        X[gameNumber][index_dict[row[1]]] = -1
        gameNumber +=1
    return(X)

gameNumber = 0
for index, row in games.iterrows():
    X[gameNumber][index_dict[row['Radiant']]] = 1
    X[gameNumber][index_dict[row['Dire']]] = -1
    gameNumber+= 1
    
def BTfit(X, Y, Teamlist, tol):
    N = len(Y)
    k = len(Teamlist)
    X = np.matrix(X)
    Xt = np.matrix.transpose(X)
    XXt = np.dot(X,Xt)
    Y = np.matrix(Y)
    Y = np.matrix.transpose(Y)
    rankings = np.matrix(np.random.rand(k,1))
    tol = 1
    t = 0
    while tol > 0.00001:
        p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
        gradient = np.matrix(np.zeros((1,k)))
        hessian = 0
        for i in range(N):
            gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
            hessian += XXt.item((i,i))*p[i]*(1-p[i])
    
        
        oldrankings = np.matrix.transpose(rankings)
        rankings = oldrankings + (1/hessian)*gradient
    
        tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
        rankings = np.matrix.transpose(rankings)
    rankings = np.exp(rankings)   
    ranks = np.asarray(rankings)
    ranks = np.ndarray.tolist(ranks)
    data = {"Teams":Teamlist, "Ranks":ranks}
    Teamskills = pd.DataFrame(data)
    return(Teamskills)
    
test = designMatrix(games, index_dict)
test2 = BTfit(test, binWins, Teamlist,1)
print(test2)
    
X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


                  Teams                  Ranks
0                    OG       [8.171956098522]
1           Team Liquid    [3.005138062074914]
2               PSG.LGD   [5.8934815680473145]
3           Team Secret    [3.244484355806005]
4           Vici Gaming    [2.053743222419171]
5         Evil Geniuses   [1.8164754709125852]
6   Royal Never Give Up   [0.9609467366877711]
7       Infamous Gaming   [1.1179869326673018]
8                Newbee   [1.6955485944337119]
9          TNC Predator   [1.7185748406980492]
10           Virtus.pro   [0.8885969891527429]
11               Fnatic   [0.8880925705885969]
12             Alliance   [1.5160745463692564]
13              Mineski   [1.8618275375343671]
14        Natus Vincere   [0.8702956023328814]
15   Chaos Esports Club  [0.45663530519673456]
16          KEEN GAMING   [0.7337385382824514]
17    Ninjas in Pyjamas   [0.3115648714795466]


In [16]:
while tol > 0.00001:
    p = np.exp(np.dot(X,rankings))/(1+np.exp(np.dot(X,rankings)))
    gradient = np.matrix(np.zeros((1,k)))
    hessian = 0
    for i in range(N):
        gradient += np.multiply(X[i],Y[i]) - np.multiply(X[i],p[i])
        hessian += XXt.item((i,i))*p[i]*(1-p[i])
        
    oldrankings = np.matrix.transpose(rankings)
    rankings = oldrankings + (1/hessian)*gradient
    
    tol = np.dot(rankings-oldrankings, np.matrix.transpose(rankings-oldrankings))
    rankings = np.matrix.transpose(rankings)

Hero Ratings

In [17]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   

In [18]:
heroes1

['Io  Tiny  Abaddon  Timbersaw  Gyrocopter',
 'Rubick  Tidehunter  Ogre Magi  Templar Assassin  Juggernaut',
 'Tidehunter  Templar Assassin  Shadow Shaman  Lifestealer  Enigma',
 'Tidehunter  Chen  Rubick  Templar Assassin  Meepo',
 'Elder Titan  Rubick  Faceless Void  Shadow Fiend  Dark Seer',
 'Elder Titan  Rubick  Sven  Dark Seer  Templar Assassin',
 'Tiny  Faceless Void  Mirana  Tinker  Shadow Demon',
 'Elder Titan  Rubick  Magnus  Wraith King  Bristleback',
 'Chen  Tidehunter  Earth Spirit  Leshrac  Meepo',
 'Chen  Alchemist  Tidehunter  Rubick  Legion Commander',
 'Shadow Demon  Sand King  Jakiro  Sven  Dragon Knight',
 "Elder Titan  Faceless Void  Pangolier  Nature's Prophet  Zeus",
 'Tiny  Omniknight  Windranger  Crystal Maiden  Bristleback',
 'Leshrac  Tidehunter  Lion  Earth Spirit  Medusa',
 'Elder Titan  Alchemist  Rubick  Ember Spirit  Dark Seer',
 'Mirana  Ogre Magi  Tidehunter  Faceless Void  Tinker',
 'Tiny  Faceless Void  Witch Doctor  Enigma  Abaddon',
 'Magnus  Shado

Firstly we need to count comparative wins separately, then we will compare them as a team

In [19]:
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

In [20]:
#Herodict goes here
l = 0
hdict = {}
for i in heroes1new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1

for i in heroes2new:
    for j in i:
        if j in hdict:
            continue
        else:
            hdict[j] = l
            l += 1
hdict

{'Io': 0,
 'Tiny': 1,
 'Abaddon': 2,
 'Timbersaw': 3,
 'Gyrocopter': 4,
 'Rubick': 5,
 'Tidehunter': 6,
 'Ogre Magi': 7,
 'Templar Assassin': 8,
 'Juggernaut': 9,
 'Shadow Shaman': 10,
 'Lifestealer': 11,
 'Enigma': 12,
 'Chen': 13,
 'Meepo': 14,
 'Elder Titan': 15,
 'Faceless Void': 16,
 'Shadow Fiend': 17,
 'Dark Seer': 18,
 'Sven': 19,
 'Mirana': 20,
 'Tinker': 21,
 'Shadow Demon': 22,
 'Magnus': 23,
 'Wraith King': 24,
 'Bristleback': 25,
 'Earth Spirit': 26,
 'Leshrac': 27,
 'Alchemist': 28,
 'Legion Commander': 29,
 'Sand King': 30,
 'Jakiro': 31,
 'Dragon Knight': 32,
 'Pangolier': 33,
 "Nature's Prophet": 34,
 'Zeus': 35,
 'Omniknight': 36,
 'Windranger': 37,
 'Crystal Maiden': 38,
 'Lion': 39,
 'Medusa': 40,
 'Ember Spirit': 41,
 'Witch Doctor': 42,
 'Silencer': 43,
 'Phantom Lancer': 44,
 'Riki': 45,
 'Ancient Apparition': 46,
 'Arc Warden': 47,
 'Centaur Warrunner': 48,
 'Enchantress': 49,
 'Invoker': 50,
 'Earthshaker': 51,
 'Oracle': 52,
 'Terrorblade': 53,
 'Lina': 54,
 '

Now to try and break down all possible matchups (which is a fuckload)

In [21]:
Matchups1 = []
binWins2 = []
for i in heroes1new:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in heroes2new:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
heroGames = pd.DataFrame(data = d)


In [22]:
"""Number of Heroes"""
k = len(hdict.keys())
""" Number of Comparisons """
N = len(binWins2)
""" Design Matrix """
X = np.zeros((N,k))
gameNumber = 0
for index, row in heroGames.iterrows():
    X[gameNumber][hdict[row['Radiant']]] = 1
    X[gameNumber][hdict[row['Dire']]] = -1
    gameNumber+= 1
test3 = designMatrix(heroGames, hdict)    

X = np.matrix(X)
Xt = np.matrix.transpose(X)
XXt = np.dot(X,Xt)
Y = np.matrix(binWins2)
Y = np.matrix.transpose(Y)
rankings = np.matrix(np.random.rand(k,1))
tol = 1.


In [23]:
ranks = np.asarray(rankings)
ranks = np.ndarray.tolist(ranks)

heroes = []
for i in hdict.keys():
    heroes.append(i)
    
data = {"Heroes":heroes, "Ranks":ranks}
data
Heroskills = pd.DataFrame(data)
Heroskills

test4 = BTfit(test3, binWins2, heroes,1)

Lets do some data fixing now on rankings and our two data frames

In [24]:
Heroskills = Heroskills.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [25]:
heroes = []
for i in hdict.keys():
    heroes.append(i)

How do we interpret the 2 ratings, for teams it is clear, but for heroes i imagine we can add up the skills of both teams and treat them as a single team, to test

for treating heroes as players in a team we refer back to Haziq

We shall first implement this for team OG, haziq does this for liverpool and we will implement this in a similar way, what is worth noting for the final potential model is that in the EPL model there are no shared players while in ours "players" will predominantly be shared

From Huang et al. 2006

In [26]:
""" Consider k individuals """
k = len(hdict.keys())
k

115

In [27]:
for i in heroes1new:
    i.sort()

In [28]:
I = []
for i in heroes1new:
    l = 0
    for j in heroes1new:
        if l == 0:
            continue
        elif i == j:
            print(True)
        l+=1
    for j in heroes2new:
        if i ==j:
            print(True)

In [29]:
ri = binWins
herodf = pd.DataFrame(data = {"Radiant": heroes1new, "Dire": heroes2new, "Winner":binWins})

In [30]:
q = np.zeros(len(hdict.keys()))
qplus = np.zeros(len(hdict.keys()))
qminus = np.zeros(len(hdict.keys()))
game = 0
for hero in hdict.keys():
    for i in range(len(binWins)):
        if hero in herodf["Radiant"][i]:
            if herodf["Winner"][i] == 1:
                q[hdict[hero]] += 1
                qplus[hdict[hero]] += 1
        elif hero in herodf["Dire"][i]:
            if herodf["Winner"][i] == 0:
                q[hdict[hero]] += 1
                qminus[hdict[hero]] += 1
        else:
            continue

In [31]:
qminus

array([ 9., 15.,  4.,  2., 15., 12., 16., 13.,  6.,  2.,  4., 13.,  6.,
        8.,  1., 27.,  9.,  2.,  2., 10., 14.,  1., 25.,  5.,  7.,  4.,
        4., 13.,  7.,  3., 13.,  4.,  4.,  4.,  1.,  0.,  5.,  7., 10.,
        7.,  3.,  9.,  4.,  0.,  1.,  0.,  7.,  2., 10., 11.,  7., 11.,
        3.,  1.,  7.,  1.,  5.,  2., 14.,  4.,  0.,  4.,  0.,  0.,  4.,
        8.,  2.,  2.,  5.,  8.,  1.,  4.,  2.,  3.,  2.,  2.,  1.,  1.,
        4.,  1.,  1.,  8.,  2.,  0.,  3.,  0.,  2.,  4.,  4.,  0.,  4.,
        0.,  0.,  0.,  0.,  1.,  1.,  2.,  0.,  3.,  0.,  0.,  6.,  0.,
        0.,  1.,  5.,  0.,  1.,  0.,  1.,  1.,  0.,  0.,  0.])

In [32]:
k = len(hdict.keys())
m = len(binWins)
Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
r = binWins
for i in heroes1new:
    for j in i:
        if binWins[l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
        l+=1
        
    l = 0
for i in heroes2new:
    for j in i:
        if binWins[l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1
    
po = np.ones(k)/k
maxiter = 1000;
delta = np.zeros(k)

def newI(team1,team2, k, m, index_dict):
    I = np.zeros((m,k))
    l = 0
    
    for i in team1:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    l = 0
    for i in team2:
        for j in i:
            I[l,index_dict[j]] = 1
        l += 1
    return(I)

def newIp(team1, k, m, index_dict):
    Ip =np.zeros((m,k))
    l = 0
    for i in team1:
        for j in i:
            Ip[l,index_dict[j]] = 1
        l+=1
    return(Ip)

def BTfit2(I,Ip,r,k,maxiter,playerlist):
    po = np.random.rand(k)
    delta = np.zeros(k)
    for t in range(maxiter):
        for i in range(k):
            pp = np.tile(np.transpose(po), (r.size,1))
            qp = np.sum(np.multiply(pp,Ip),axis=1)
            Ipp = Ip[:,i]
            q = np.sum(np.multiply(pp,I),axis=1)
            Ii = I[:,i]
            Ipp = Ipp.astype(int)
            Ii = Ii.astype(int)
            delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
            if np.isnan(delta[i]):
                print(po)
                print(delta)
                print(qp[Ipp])
                print(q[Ii])
                break
            po[i] = delta[i]*po[i]
            po = po/np.sum(po)
        if np.max(np.abs(delta-1)) < 0.001:
            separate = t*k
            break
    pest = po
    data = {"Heroes":playerlist, "Ranks":pest}
    Heroskills2 = pd.DataFrame(data)
    return(Heroskills2)
    
    
    
    
for t in range(maxiter):
    for i in range(k):
        pp = np.tile(np.transpose(po), (binWins.size,1))
        qp = np.sum(np.multiply(pp,Ip),axis=1)
        Ipp = Ip[:,i]
        q = np.sum(np.multiply(pp,I),axis=1)
        Ii = I[:,i]
        Ipp = Ipp.astype(int)
        Ii = Ii.astype(int)
        delta[i] = np.sum(np.divide(r[Ipp],qp[Ipp]))/np.sum(np.divide(r[Ii],q[Ii]))
        if np.isnan(delta[i]):
            print(po)
            print(delta)
            print(qp[Ipp])
            print(q[Ii])
            break
        po[i] = delta[i]*po[i]
        po = po/np.sum(po)
    if np.max(np.abs(delta-1)) < 0.001:
        separate = t*k
        break
pest = po                        
        
        
test5 = BTfit2(I,Ip,binWins,k,10,heroes)
test5


Heroes     Ranks
0                  Io  0.003704
1                Tiny  0.005961
2             Abaddon  0.005845
3           Timbersaw  0.004891
4          Gyrocopter  0.002145
5              Rubick  0.000601
6          Tidehunter  0.019730
7           Ogre Magi  0.025347
8    Templar Assassin  0.005913
9          Juggernaut  0.006581
10      Shadow Shaman  0.001704
11        Lifestealer  0.030500
12             Enigma  0.002134
13               Chen  0.006573
14              Meepo  0.004710
15        Elder Titan  0.024969
16      Faceless Void  0.015642
17       Shadow Fiend  0.002913
18          Dark Seer  0.002693
19               Sven  0.019481
20             Mirana  0.009939
21             Tinker  0.000981
22       Shadow Demon  0.040212
23             Magnus  0.019041
24        Wraith King  0.004867
25        Bristleback  0.004622
26       Earth Spirit  0.000999
27            Leshrac  0.008360
28          Alchemist  0.012313
29   Legion Commander  0.006517
..                ...       ...
85        Drow Ranger  0.004296
86      Skywrath Mage  0.000794
87        Dark Willow  0.004054
88         Naga Siren  0.012037
89            Undying  0.009455
90            Spectre  0.005277
91              Pudge  0.005477
92             Clinkz  0.008081
93        Bloodseeker  0.014703
94       Chaos Knight  0.008206
95              Viper  0.008410
96               Bane  0.002924
97            Slardar  0.014363
98             Huskar  0.009515
99      Troll Warlord  0.006130
100        Lone Druid  0.015000
101   Vengeful Spirit  0.014443
102  Treant Protector  0.013466
103            Dazzle  0.004445
104         Disruptor  0.014548
105           Phoenix  0.015821
106              Tusk  0.008458
107              Luna  0.004370
108              Doom  0.005953
109             Lycan  0.006284
110    Spirit Breaker  0.013087
111     Night Stalker  0.005168
112     Bounty Hunter  0.011657
113        Venomancer  0.001486
114      Ember Spirit  0.006874

[115 rows x 2 columns]

Start with initial p_j^0 > 0, j = 1,...,k and obtain corresponding qi's values for i = 1,...,m
k = no.heros
m = no.games



In [33]:
pest/np.min(pest)

array([4.15664897e+09, 1.41287231e+33, 5.33880590e+11, 3.99665343e+11,
       4.88251635e+30, 1.96090336e+22, 1.65747722e+20, 2.96461388e+51,
       1.19650899e+07, 2.54963297e+16, 5.26780997e+11, 2.95649552e+51,
       1.63430311e+19, 9.51048945e+11, 2.01538297e+02, 2.54002755e+41,
       1.25849115e+12, 1.74403607e+09, 1.96198420e+02, 1.06117961e+22,
       1.80841981e+25, 3.71407042e+04, 2.30092479e+58, 1.23375512e+19,
       1.14492409e+07, 9.61707643e+06, 5.84230717e+11, 3.88779057e+43,
       7.62887277e+11, 8.28408963e+13, 8.88777828e+24, 3.56096971e+16,
       4.22955878e+04, 2.88548941e+16, 7.18560061e+06, 3.19806179e+04,
       1.39308225e+14, 1.28617477e+07, 1.12159925e+22, 3.28002371e+09,
       4.38726091e+04, 8.39145507e+21, 2.30155883e+09, 6.46071095e+13,
       1.46344116e+09, 1.89703843e+02, 4.79795770e+21, 2.05132107e+02,
       3.65391315e+24, 5.50679359e+14, 9.58072809e+11, 1.75960621e+27,
       2.00996632e+09, 7.73804043e+06, 1.40214435e+24, 7.73804043e+06,
      

In [34]:
data = {"Heroes":heroes, "Ranks":pest}
data
Heroskills2 =test5
Heroskills2

Heroes     Ranks
0                  Io  0.003704
1                Tiny  0.005961
2             Abaddon  0.005845
3           Timbersaw  0.004891
4          Gyrocopter  0.002145
5              Rubick  0.000601
6          Tidehunter  0.019730
7           Ogre Magi  0.025347
8    Templar Assassin  0.005913
9          Juggernaut  0.006581
10      Shadow Shaman  0.001704
11        Lifestealer  0.030500
12             Enigma  0.002134
13               Chen  0.006573
14              Meepo  0.004710
15        Elder Titan  0.024969
16      Faceless Void  0.015642
17       Shadow Fiend  0.002913
18          Dark Seer  0.002693
19               Sven  0.019481
20             Mirana  0.009939
21             Tinker  0.000981
22       Shadow Demon  0.040212
23             Magnus  0.019041
24        Wraith King  0.004867
25        Bristleback  0.004622
26       Earth Spirit  0.000999
27            Leshrac  0.008360
28          Alchemist  0.012313
29   Legion Commander  0.006517
..                ...       ...
85        Drow Ranger  0.004296
86      Skywrath Mage  0.000794
87        Dark Willow  0.004054
88         Naga Siren  0.012037
89            Undying  0.009455
90            Spectre  0.005277
91              Pudge  0.005477
92             Clinkz  0.008081
93        Bloodseeker  0.014703
94       Chaos Knight  0.008206
95              Viper  0.008410
96               Bane  0.002924
97            Slardar  0.014363
98             Huskar  0.009515
99      Troll Warlord  0.006130
100        Lone Druid  0.015000
101   Vengeful Spirit  0.014443
102  Treant Protector  0.013466
103            Dazzle  0.004445
104         Disruptor  0.014548
105           Phoenix  0.015821
106              Tusk  0.008458
107              Luna  0.004370
108              Doom  0.005953
109             Lycan  0.006284
110    Spirit Breaker  0.013087
111     Night Stalker  0.005168
112     Bounty Hunter  0.011657
113        Venomancer  0.001486
114      Ember Spirit  0.006874

[115 rows x 2 columns]

Compare these results to overall pick rate, and how it changes over time as the model begins to converge

Cool, so we've implemented two models for hero weighting, likely should implement the combined model now, additionally should place these into functions so that we can develop train/test data for analytics

Combined Model: The idea behind the comparative model is to treat the heroes picked in the game as a homeground advantage by seeing which composition has the highest win-probability according to previous model (sum of player skills is the teams skill independent of which team is playing) additionally there is likely ways to treat it as a second logistic parameter but ya boi dumb so...

Imma do this with directly optimizing the log likelihood cause i a lazy bitch

In [35]:
"aij be the number of times i beats j at home"
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(binWins)

def BTloglik(li):
    lilj = np.zeros(len(li[:-1]))
    for i in range(len(li[:-1])):
        for j in range(len(li[:-1])):
            if i != j:
                lilj[i] += (li[-1]*li[i]+li[j])
    print(lilj)
    ll = c*np.log(li[-1]) + np.sum(np.multiply(wincounts,np.log(li[:-1])))-np.sum(np.dot(nij,np.log(lilj)))
    return(-ll)

x0 = np.random.rand(k+1)
len(x0[:-1])
wincounts
#np.multiply(Wi,x0[:-2])
BTloglik(x0)


[9.33390117 9.09133174 9.24524245 8.95841502 9.02273712 8.82372283
 9.01734876 9.30044122 8.84240859 9.11896321 9.06604567 8.95006423
 9.18173502 9.07509314 8.82885892 8.88947801 9.3010314  9.33826291]


866.7125960696956

In [36]:
from scipy.optimize import minimize

In [37]:
np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

  9.26224688 11.40682367 16.10872218 10.97845771 22.73270083 12.91782388]
[36.9769191  18.18695954 14.36576913 15.32058476 21.64011969 16.71884406
 28.42515164 19.29109094 23.04746824 15.6920382  26.70349369 22.95552071
  9.21123019 11.51694053 15.90181363 10.55522984 22.68495571 12.68515139]
[37.30493266 18.3183206  14.48233209 15.41160912 22.22044614 17.18720201
 28.62367683 19.40267597 22.80106247 16.29248671 26.95329214 22.89431329
  9.21913498 11.40383823 15.6629885  11.04270116 22.7787849  12.52169927]
[35.79242438 18.09751106 14.29546699 15.21235918 21.43206265 17.00345046
 28.14922932 19.3101646  22.82128533 16.34692122 26.57670895 22.6859864
  9.25571227 11.39703889 15.84281965 11.78602281 22.62981201 13.24548159]
[36.50536444 18.33440363 14.38480593 15.53174761 21.41381053 16.79830899
 28.20002786 19.64819081 24.54104263 15.81771309 26.67815003 23.16264448
  9.22491379 11.40039941 15.73258199  9.16986599 22.87746099 12.41082762]
[36.939832   18.16726861 14.38855166 15.2327180

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log



[36.13049067 18.2185781  14.4324248  15.35189872 20.93071425 14.91331695
 28.77649733 18.64534122 20.74560166 15.34916658 26.61448105 19.60469753
  8.86927272 11.03393062 15.99149507 11.97643078 21.44751023  9.7569731 ]
[35.37336597 18.08547384 14.40521555 15.10585429 20.65855137 14.70100815
 28.80117882 18.22867278 19.18820483 15.39574351 26.58407809 19.00437446
  8.82390785 10.97001214 15.9711931  13.61608625 21.20974772  9.51645784]
[36.10253369 18.24790051 14.39327472 15.33421873 21.18590573 15.88567157
 28.58154232 18.97259631 22.1381501  15.86279409 26.72977959 21.55193594
  9.06081181 11.23909746 15.91657737 11.44165839 22.03429677 11.44904413]
[36.45396824 18.44771753 14.63613076 15.49898356 21.00006752 14.68599395
 28.90827621 18.65101042 20.43567093 15.48882571 27.23863136 19.79494213
  8.80910901 11.02622646 16.05443623 11.95480988 21.3794367   8.89288566]
[35.6242806  18.09194081 14.29872313 15.16366045 21.02579432 15.85328834
 28.54316063 18.77183477 21.51794628 15.809423

  8.24071048 10.46574838 13.64691254  9.90677414 15.05106084  9.81112452]
[22.31323509 14.7354915  13.63495323 14.57370867 16.81086273 13.65402305
 28.584013   14.8652095  16.40446955 13.39000774 19.75238256 14.39712936
  8.13256258 10.34301691 13.29241365  9.16678551 14.06612662  9.65630108]
[20.87119754 14.9758311  13.46480048 14.40946946 16.66448787 13.33907509
 28.50460127 14.08328208 15.66252152 14.46934133 19.76300486 15.76221566
  8.1778129  10.29092853 13.55361043 10.98693145 15.21993659  8.8983614 ]
[23.26008369 15.13683226 13.55395095 14.6654856  16.74239229 13.83881988
 28.93352199 14.65451252 16.19014111 14.13881747 20.49260134 15.10777011
  8.22486841 10.31331244 13.83168599 10.67582815 14.94419301  9.53071922]
[20.41170996 15.01777777 13.54988857 14.58977014 17.55019223 14.18952133
 29.48233708 14.90615347 16.46561669 14.32447371 20.21252242 15.54492381
  8.24161479 10.47290455 13.60184529 10.35040015 14.56528936 10.389602  ]
[21.56826026 15.16075071 13.55108312 14.585822

...

  4.27388285  7.2047187  10.4325067   4.87724606  6.52599406  4.92395096]
[10.79551937  9.89270229  8.76295681  9.15885302  7.56256973  6.65206433
  7.09650366  6.06710215  7.30364333  7.0298918   5.82284098  6.42039348
  4.20736256  7.20385895 10.24597     4.77511748  6.50917887  5.00071557]
[11.21342693 10.04473181  8.76276622  9.14425894  7.72809672  6.6227282
  7.11181827  6.22994802  7.43438061  7.27154883  5.9167516   6.80166311
  4.25009964  7.26744162 10.51415163  4.89173443  6.47412911  4.97775134]
[11.12607959 10.05138553  8.93922867  9.20202103  7.85206537  6.80115118
  7.25609948  6.08556537  7.68717351  7.4189451   5.7882732   6.50550182
  4.26315923  7.22260608 10.31112253  4.88187213  6.45183632  4.92243901]
[10.80099747  9.9819271   8.83094058  9.14523136  7.66622299  6.62639426
  7.29781754  6.15043567  7.50611287  7.07768572  5.76409059  6.55942824
  4.23710542  7.15765356 10.22391549  4.97823614  6.42555101  4.93330414]
[10.53033118  9.86191832  8.66902686  9.0005221

 4.11108587 7.24116926 9.24576861 4.58174817 5.75973934 4.68342602]
[9.61383426 8.89373135 7.34471995 8.24295392 7.80004688 6.63239657
 6.77402253 5.95916506 6.86058474 6.51727912 5.35084319 6.27826443
 4.09177437 7.26053638 9.06475338 4.56635822 5.76447991 4.65470723]
[9.57537409 8.86103322 7.30156252 8.23021238 7.8603359  6.75049869
 6.79659556 5.95501892 6.83168283 6.5551667  5.29157486 6.39794756
 4.09622071 7.28857324 8.95365189 4.542853   5.80472168 4.64667535]
[9.78841691 9.12353092 7.58914296 8.36465655 7.73882975 6.64338209
 6.83603576 6.15024728 7.14530058 6.54109642 5.4973575  6.33602197
 4.1341082  7.19126814 9.41488791 4.61512755 5.70463047 4.80799542]
[9.49498314 8.85696864 7.25760952 8.13742502 7.6765813  6.3945329
 6.63163993 5.85393237 6.76760912 6.1948025  5.32921572 6.01789432
 4.04027086 7.17419516 9.0264948  4.57716982 5.59999296 4.54934546]
[9.49252932 8.72955817 7.17446892 8.1306639  7.73132007 6.38149798
 6.65128632 5.77043918 6.62953304 6.36824653 5.30898779 5.

[9.80082652 8.97380365 7.36068175 8.20730964 7.87743248 6.6584917
 6.70597047 5.94563316 6.85620548 6.32461626 5.41142012 6.26220665
 4.09076427 7.25506486 9.06480059 4.54123044 5.655965   4.77507488]
[9.55116207 8.76375868 7.16586262 8.18564512 7.73402601 6.55676045
 6.75735043 5.81163747 6.90888417 6.33953445 5.35461494 6.11867702
 4.06295405 7.25896166 8.98069888 4.55597381 5.62871666 4.61001605]
[9.69000777 8.81470233 7.27790428 8.23276397 7.82860788 6.58362511
 6.88780026 5.92830604 6.89632783 6.32515368 5.31237404 6.26252267
 4.0858262  7.28699607 8.88649359 4.53824466 5.74113319 4.65763142]
[9.80483076 8.87934313 7.27712358 8.32790767 7.74371796 6.63648978
 6.83677922 5.88319972 7.03739116 6.31142214 5.36609133 6.31652149
 4.07894724 7.30809295 9.07521946 4.52577074 5.71295589 4.63654086]
[9.63895887 8.87930945 7.24984688 8.1370462  7.81246908 6.53933395
 6.79517752 5.8390685  6.84161759 6.33471328 5.37708191 6.26666885
 4.07891135 7.2243794  9.00630247 4.57629305 5.56187217 4.5

[9.66146681 9.03654199 7.41033601 8.2754951  8.07190474 6.69625497
 6.84724143 5.8486961  7.23208306 6.34843749 5.39364397 6.29817257
 4.09649776 7.29714028 9.03070209 4.58481858 5.658099   4.73539661]
[9.63679192 9.00610816 7.40019353 8.23373676 8.0980791  6.63208484
 6.81425215 5.86984955 7.09639028 6.38000926 5.3781414  6.24205657
 4.08992085 7.30611545 9.00387206 4.58859133 5.66110953 4.75290501]
[9.7000862  8.98459524 7.38051119 8.26944745 8.04457432 6.62339102
 6.82988529 5.86810771 7.12177264 6.38233666 5.36787827 6.30676331
 4.08969473 7.32585929 9.03335888 4.5573059  5.68172942 4.75463426]
[9.63375326 8.95949186 7.37823423 8.26888251 8.09331144 6.69510457
 6.8929481  5.87576088 7.15292612 6.45813505 5.38997607 6.28678411
 4.1027608  7.33439683 8.98634057 4.57492938 5.7005189  4.77748717]
[9.67917029 9.01126304 7.38268383 8.28474422 8.10795389 6.67315491
 6.86448464 5.84989809 7.24298462 6.38963466 5.43052418 6.26024784
 4.09645181 7.33612587 9.05696521 4.57487608 5.65659726 4.

[9.76978223 9.0296797  7.42667219 8.2784134  8.15126557 6.62386399
 6.96399951 5.8313194  7.16471445 6.44841456 5.41541731 6.3770943
 4.10771069 7.34363271 9.03037285 4.59098136 5.65181251 4.77070996]
[9.82593274 9.0432028  7.45112167 8.28820462 8.23072411 6.58007839
 6.9406673  5.86258323 7.25770853 6.47509232 5.3910331  6.3368182
 4.10932285 7.36763296 9.01829563 4.58414195 5.69416858 4.76498177]
[9.8966829  9.06694038 7.48366168 8.30998385 8.27553208 6.55344228
 6.97606331 5.89757701 7.29367399 6.51900665 5.39278366 6.36266952
 4.11657406 7.38692421 9.03593443 4.59591575 5.72211002 4.7573    ]
[9.75245541 8.94335447 7.37381176 8.26183125 8.14295902 6.59100383
 6.93736325 5.8612499  7.23081007 6.41560854 5.37465473 6.26407319
 4.10339034 7.35109564 8.95062706 4.54725632 5.66872786 4.78158921]
[9.80836476 8.991082   7.40527606 8.23880214 8.18237606 6.56126085
 6.89391107 5.80217355 7.12789038 6.46713118 5.37499201 6.34092605
 4.10252962 7.35536437 8.96727239 4.56035366 5.7051014  4.75

In [38]:
data = {"Teams":Teamlist, "Ranks":res.x[:-1]/np.min(res.x[:-1]),"Radiant Advantage":res.x[-1]}
data
Teamhg = pd.DataFrame(data)
Teamhg.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg

Teams      Ranks  Radiant Advantage
0                    OG  18.053787           0.915161
1           Team Liquid  15.822115           0.915161
14        Natus Vincere  15.641570           0.915161
3           Team Secret  13.610140           0.915161
4           Vici Gaming  13.523732           0.915161
2               PSG.LGD  11.035274           0.915161
13              Mineski  10.865921           0.915161
8                Newbee  10.634655           0.915161
6   Royal Never Give Up   9.441427           0.915161
5         Evil Geniuses   8.551742           0.915161
9          TNC Predator   8.062199           0.915161
11               Fnatic   7.491167           0.915161
7       Infamous Gaming   6.233234           0.915161
16          KEEN GAMING   5.833543           0.915161
10           Virtus.pro   4.816592           0.915161
17    Ninjas in Pyjamas   3.058589           0.915161
15   Chaos Esports Club   2.348975           0.915161
12             Alliance   1.000000           0.915161

In [39]:
np.sum(aij,axis=1)

array([ 8., 13.,  3.,  8.,  7.,  4.,  5.,  2.,  7.,  5.,  2.,  5.,  4.,
        5.,  5.,  1.,  3.,  2.])

In [40]:
Teamlist

['OG',
 'Team Liquid',
 'PSG.LGD',
 'Team Secret',
 'Vici Gaming',
 'Evil Geniuses',
 'Royal Never Give Up',
 'Infamous Gaming',
 'Newbee',
 'TNC Predator',
 'Virtus.pro',
 'Fnatic',
 'Alliance',
 'Mineski',
 'Natus Vincere',
 'Chaos Esports Club',
 'KEEN GAMING',
 'Ninjas in Pyjamas']

In [41]:
np.sum(bij,axis=1)

array([1., 9., 3., 6., 5., 2., 8., 5., 7., 8., 7., 8., 3., 5., 5., 5., 8.,
       9.])

Lets add some extra data to represent whether a team's composition has won

In [42]:
Teamskill1 = np.zeros(m)
Teamskill2 = np.zeros(m)

index = 0
for i in heroes1new:
    for j in i:
        Teamskill1[index] += test4["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in heroes2new:
    for j in i:
        Teamskill2[index] += test4["Ranks"][hdict[j]][0]
    index += 1

In [43]:
Teamwin1 = np.zeros(m)
for i in range(m):
    prob = Teamskill1[i]/(Teamskill1[i]+Teamskill2[i])
    if prob >= 0.5:
        Teamwin1[i] = 1

In [44]:
Teamwin1

array([0., 1., 1., 1., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 1., 1., 1.,
       0., 1., 0., 1., 1., 0., 0., 1., 0., 1., 0., 1., 0., 0., 0., 0., 1.,
       1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 1.,
       1., 0., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 1., 0., 1., 1., 1.,
       1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 1., 0.,
       0., 0., 1., 1., 0., 1., 0., 1., 1., 1., 1., 1., 1., 1., 0., 0., 0.,
       0., 1., 0., 0., 1., 1., 0., 1., 1., 1., 0., 1., 0., 1., 1., 0., 0.,
       0., 0., 1., 0., 0., 0., 0., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1.,
       0., 1., 1., 0., 0., 1., 1., 1., 0., 0., 1., 0., 0., 1., 1., 1., 0.,
       1., 1., 0., 1., 0., 1., 0., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0.,
       0., 1., 1., 0., 1., 1., 0., 1., 0., 1., 0., 0., 0., 0., 1., 0., 1.,
       1., 0., 1., 0., 1., 1.])

In [45]:
games['Team Winner'] = Teamwin1

In [46]:
Teamskill3 = np.zeros(m)
Teamskill4 = np.zeros(m)

index = 0
m = len(games["Winner"])
for i in heroes1new:
    for j in i:
            Teamskill3[index] += Heroskills2["Ranks"][hdict[j]]
    index += 1

index = 0
for i in heroes2new:
    for j in i:
            Teamskill4[index] += Heroskills2["Ranks"][hdict[j]]            
    index += 1

Teamskill3

array([0.02254577, 0.05817135, 0.05998018, 0.03752685, 0.04681843,
       0.05365738, 0.07273513, 0.05410094, 0.04037117, 0.04573411,
       0.08127486, 0.04968234, 0.03505289, 0.03699179, 0.04087943,
       0.07163857, 0.02981734, 0.05743711, 0.01047814, 0.06845074,
       0.03630977, 0.06309784, 0.03692672, 0.03916256, 0.02946617,
       0.04939007, 0.04356383, 0.03123821, 0.09418845, 0.03603243,
       0.05698975, 0.06166621, 0.06502408, 0.09306525, 0.06843422,
       0.05731427, 0.08838348, 0.04740502, 0.08999948, 0.07231366,
       0.04909045, 0.01400748, 0.03147985, 0.06298788, 0.06935162,
       0.04590914, 0.04054103, 0.04213315, 0.06730373, 0.05527248,
       0.04229549, 0.04572812, 0.05542586, 0.05396386, 0.05653596,
       0.05630962, 0.06695653, 0.04562867, 0.03742788, 0.05185827,
       0.0383483 , 0.06694648, 0.03779197, 0.06739197, 0.01995157,
       0.03641113, 0.06849765, 0.02504429, 0.02282785, 0.06798504,
       0.0787684 , 0.0744901 , 0.05466537, 0.03414476, 0.04005

In [47]:
Teamwin2 = np.zeros(m)
for i in range(m):
    if Teamskill3[i] > Teamskill4[i]:
        Teamwin2[i] = 1

Teamwin2

array([0., 1., 1., 0., 1., 0., 1., 1., 0., 0., 1., 1., 0., 0., 0., 0., 0.,
       0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 1., 1., 1.,
       0., 0., 1., 0., 1., 1., 0., 0., 0., 1., 0., 0., 0., 0., 1., 0., 0.,
       1., 1., 0., 0., 1., 1., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0.,
       0., 1., 1., 1., 0., 0., 1., 1., 0., 1., 1., 0., 0., 1., 0., 0., 0.,
       1., 0., 1., 1., 0., 0., 0., 1., 1., 0., 0., 0., 1., 1., 0., 0., 1.,
       0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 1., 0., 1., 0., 0., 1., 1.,
       0., 1., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 0., 0., 0., 1.,
       1., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 0., 1., 0., 1., 0., 1.,
       0., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 1., 0., 0., 0., 0., 0.,
       0., 0., 1., 0., 0., 1., 1., 1., 1., 1., 0., 1., 1., 0., 0., 0., 1.,
       0., 0., 0., 1., 1., 1.])

In [48]:
games['Team Winner 2'] = Teamwin2

In [49]:
k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}

Teamhg2 = pd.DataFrame(data)
Teamhg2.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 0
for i in games["Radiant"]:
    j = games["Dire"][l]
    if games["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(games["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 2":np.exp(res.x[-1])}

Teamhg3 = pd.DataFrame(data)
Teamhg3.sort_values(by=['Ranks'], inplace=True, ascending=False)
Teamhg3


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log


[26.67501292 14.34406435 13.12880559 12.65261109 15.89980811 18.60401185
 22.30209269 15.40289269 21.61998393 13.81557939 19.69562041 20.70525242
  9.21039443 12.31971292 14.64513421 10.11057058 16.24859578 23.7643553 ]
[27.55908149 14.71961211 13.38684391 12.95606277 16.83505843 18.97151123
 22.75958247 16.33202618 22.11901368 14.04700484 20.62918451 21.94996169
  9.23470363 12.33304646 14.98197152  9.45848564 16.71441974 25.24132203]
[26.62478944 14.61923235 13.2141539  12.87262642 16.70381755 18.70736366
 22.67816559 16.59090834 21.66927417 14.53569658 20.42196439 21.8120208
  9.36394791 12.22045547 14.76594832 10.75211025 17.09656866 24.3542815 ]
[26.89364525 14.44430945 13.18324431 12.70656023 16.10151768 18.46630217
 22.46745411 15.88519455 21.60996637 14.09931757 20.87497781 20.32991927
  9.20692003 12.31942104 14.71701627  9.81608088 16.17285656 23.76714949]
[26.77146061 14.33992372 13.20767499 12.56498388 15.87841761 18.71614284
 22.01819695 15.35511268 21.70250645 13.56025687

  8.50207995 10.58112409 11.79715846  9.33504921 18.40498424 12.02374288]
[18.13473962 13.51619874 13.45645844 11.60116713 13.68369346 12.93563212
 15.69316599 14.76645038 19.27302727 13.40852359 12.98267685 18.41366679
  8.50461546 10.37438886 11.62937727  9.4659606  19.19046722 11.6686127 ]
[18.6711218  13.06915364 13.06943133 11.61191998 12.81730873 13.19589022
 16.70494108 13.03259122 18.66639736 12.78485947 13.34413719 17.45225652
  8.42813871 10.64710249 11.77884721  8.81972122 17.84526639 11.97281299]
[18.47803543 12.8311624  12.87435193 11.33818126 11.95511526 12.86599702
 16.57228294 13.63982366 18.36656435 13.28463436 14.13682532 15.99934695
  8.3786355  10.78659386 11.68581991  9.17357111 17.31672105  9.8822468 ]
[20.39354751 13.48865477 13.3496015  11.76477907 13.20682686 14.40148235
 17.26131824 13.41655947 19.87545651 13.37478243 14.32747693 17.78976678
  8.51914112 11.03583035 12.30249554  8.99644447 18.13452713 13.37254616]
[18.95169287 13.4630053  13.45225449 11.839757

[17.85114892 14.02561298 15.17541843 11.03791136 12.29288058 11.04850413
 12.6191449  11.78695287 21.95643631 12.27511898 14.0982879  15.61060347
  7.5815149  10.12390733 10.27247054  8.40944768 17.08321755 10.56286468]
[17.61927974 14.00317815 15.25349206 11.14632639 12.25762921 11.01177142
 12.56925185 11.58048165 22.06483491 12.25566978 13.67540225 16.45341578
  7.546849   10.09848409 10.19682545  8.33816858 16.55113812 10.64020048]
[18.00522927 14.40899136 15.2873606  11.16040668 13.10451355 11.04466376
 13.01852177 12.48245575 22.15992772 12.99987511 14.54244678 16.67307648
  7.7088832  10.15391633 10.4699278   8.50084591 17.68165901 11.04428686]
[18.53439252 13.96303835 14.93890955 11.12677542 12.37212948 11.54714079
 13.02590857 11.61991727 21.70456924 12.31614336 13.88961059 15.98771168
  7.69140666 10.25775424 10.56331611  8.18958062 17.17670083 11.42019439]
[18.42402055 13.65561358 14.62155349 11.1091333  11.90225698 11.46980327
 13.38876353 11.36726597 21.40734165 12.5149098

...

[ 9.05152705 10.19075005  7.45256912  8.99839105  7.21790786  6.14934587
  6.21752236  6.37242998  6.64511778  7.36135393  6.00952278  6.31327282
  4.42685316  8.25884253  5.59588966  4.63016963  5.2692152   5.15491796]
[ 9.3781831  10.67340691  8.02164678  9.26920043  7.58159814  6.38545202
  6.634181    6.42730441  7.00298698  7.55600814  6.20437288  6.63820552
  4.5576368   8.28590201  5.68152064  4.83772556  5.48087607  5.26192015]
[ 9.20678012 10.21575257  7.68899496  9.28462879  7.43191524  6.26631258
  6.38210712  6.2455965   6.82147669  7.23980041  5.98672442  6.54675459
  4.45250411  8.38367092  5.68053994  4.72796882  5.48994357  5.18552854]
[ 9.16481531 10.10294432  7.6802581   9.35529851  7.49022849  6.25540157
  6.29875209  6.13483651  6.73570461  7.057235    5.83748324  6.59893274
  4.41478432  8.43722402  5.63099941  4.69619784  5.53005409  5.1058726 ]
[ 9.24892971 10.26238106  7.6428247   9.26668938  7.29676558  6.12442643
  6.77746723  6.31632959  6.87718587  7.4236673

[ 9.40277697 10.41897171  7.35132068  8.93495119  7.40197142  6.32110264
  6.45077536  6.33828024  7.03115016  6.90971631  5.95943364  6.41234383
  4.44585888  8.32174913  5.52962006  4.71016516  5.41168764  4.9729622 ]
[ 9.29333455 10.29763497  7.23655367  8.85278716  7.26912562  6.21565979
  6.40359274  6.30855708  6.91756237  6.76880823  5.92975342  6.28276028
  4.39679002  8.3054428   5.43455394  4.60833018  5.33972164  4.90620686]
[ 9.35733352 10.28986455  7.25573821  8.87897145  7.34971433  6.31053628
  6.42224416  6.3432844   6.94294313  6.84560906  5.95385275  6.32802313
  4.42049854  8.31266869  5.47176821  4.64216478  5.35949581  4.97910171]
[ 9.40440538 10.23805782  7.25055276  8.8912947   7.36647238  6.35608681
  6.45052991  6.37771038  6.975811    6.85056009  5.95331765  6.33435141
  4.42682982  8.32215271  5.4689697   4.64134955  5.37396179  5.01140343]
[ 9.38429119 10.22873677  7.32854251  8.9814394   7.35712225  6.29695352
  6.36352065  6.29137961  6.98665042  6.9006061

[ 9.43881864 10.49978255  7.33006159  8.81840018  7.348149    6.42260042
  6.46911083  6.3083876   7.15327237  6.84591961  6.02870266  6.34030773
  4.46306824  8.29069955  5.49755867  4.72831609  5.47088478  5.04534966]
[ 9.40813608 10.48669296  7.28217637  8.76928259  7.30862142  6.35967851
  6.45745437  6.31945425  7.09552084  6.84101929  6.02690123  6.29728849
  4.45222228  8.27133647  5.46991092  4.70442434  5.44330305  5.03189492]
[ 9.40747    10.48331974  7.27799887  8.75261628  7.28056814  6.33914078
  6.47797722  6.32583539  7.08565779  6.84735183  6.02585017  6.27741739
  4.45114157  8.26402817  5.46005618  4.70285505  5.44851815  5.04092012]
[ 9.35239009 10.41142007  7.27471365  8.79320045  7.26934439  6.34400729
  6.40629776  6.2915651   7.05381345  6.85573556  5.99965934  6.24954507
  4.43393805  8.28429192  5.4723799   4.68704127  5.39782222  5.00714144]
[ 9.40876298 10.45140735  7.28553295  8.77628115  7.26857318  6.38058692
  6.41234473  6.305722    7.10695377  6.8064736

  4.50771843  8.22023849  5.60284482  4.66852394  5.63444463  5.08196464]
[ 9.5803386  10.78213056  7.37878441  8.61952364  7.30006268  6.46882354
  6.56109218  6.13113981  7.00080718  7.012244    5.87681867  6.19513157
  4.48110124  8.20436789  5.52640054  4.64935555  5.51677215  5.09251647]
[ 9.53327044 10.76496602  7.37663284  8.62781594  7.32134155  6.44835031
  6.64411518  6.10343325  7.04578241  7.0905848   5.84115671  6.22084093
  4.48132798  8.22404486  5.51557407  4.6566265   5.48598979  5.13220316]
[ 9.68806374 10.92355965  7.34977359  8.56665875  7.37540354  6.53082537
  6.46471993  6.1400749   6.96475701  6.93847498  5.89697739  6.23090564
  4.49918369  8.17435903  5.56792893  4.65301102  5.58745183  5.04885197]
[ 9.66086184 10.92227607  7.47073827  8.61880995  7.31990598  6.46679965
  6.53274771  6.20394503  6.99448971  6.99576278  5.94989437  6.1510042
  4.49771958  8.16878557  5.54732659  4.65607023  5.5546743   5.03131072]
[ 9.68968917 11.02902241  7.55918754  8.6297862

Teams     Ranks  Draft Advantage 2
1           Team Liquid  1.734899           2.183858
0                    OG  1.590054           2.183858
3           Team Secret  1.448434           2.183858
13              Mineski  1.400983           2.183858
2               PSG.LGD  1.313985           2.183858
4           Vici Gaming  1.300992           2.183858
8                Newbee  1.275033           2.183858
9          TNC Predator  1.274558           2.183858
6   Royal Never Give Up  1.216561           2.183858
5         Evil Geniuses  1.210513           2.183858
11               Fnatic  1.196881           2.183858
7       Infamous Gaming  1.186665           2.183858
10           Virtus.pro  1.163667           2.183858
14        Natus Vincere  1.132916           2.183858
16          KEEN GAMING  1.131965           2.183858
17    Ninjas in Pyjamas  1.092725           2.183858
15   Chaos Esports Club  1.045561           2.183858
12             Alliance  1.037158           2.183858

In [50]:
Teamhg3

Teams     Ranks  Draft Advantage 2
1           Team Liquid  1.734899           2.183858
0                    OG  1.590054           2.183858
3           Team Secret  1.448434           2.183858
13              Mineski  1.400983           2.183858
2               PSG.LGD  1.313985           2.183858
4           Vici Gaming  1.300992           2.183858
8                Newbee  1.275033           2.183858
9          TNC Predator  1.274558           2.183858
6   Royal Never Give Up  1.216561           2.183858
5         Evil Geniuses  1.210513           2.183858
11               Fnatic  1.196881           2.183858
7       Infamous Gaming  1.186665           2.183858
10           Virtus.pro  1.163667           2.183858
14        Natus Vincere  1.132916           2.183858
16          KEEN GAMING  1.131965           2.183858
17    Ninjas in Pyjamas  1.092725           2.183858
15   Chaos Esports Club  1.045561           2.183858
12             Alliance  1.037158           2.183858

In [94]:
Teamhg2

Teams     Ranks  Draft Advantage 1
8                Newbee  1.982305           2.803456
13              Mineski  1.734117           2.803456
4           Vici Gaming  1.560800           2.803456
0                    OG  1.548791           2.803456
2               PSG.LGD  1.392951           2.803456
3           Team Secret  1.383531           2.803456
1           Team Liquid  1.357961           2.803456
6   Royal Never Give Up  1.307455           2.803456
9          TNC Predator  1.302224           2.803456
11               Fnatic  1.269619           2.803456
7       Infamous Gaming  1.236808           2.803456
10           Virtus.pro  1.225983           2.803456
14        Natus Vincere  1.225852           2.803456
5         Evil Geniuses  1.205772           2.803456
16          KEEN GAMING  1.175462           2.803456
17    Ninjas in Pyjamas  1.127815           2.803456
15   Chaos Esports Club  1.045007           2.803456
12             Alliance  1.013898           2.803456

In [52]:
import random
Train = random.sample(range(193), 97)
Train
total = range(193)
Test = []
for i in total:
    if i not in Train:
        Test.append(i)
Test

trainRadiant = games["Radiant"][97:]
trainDire = games["Dire"][97:]
trainWinner = games["Winner"][97:]

trainGames = pd.DataFrame(data = {'Radiant':trainRadiant,'Dire':trainDire,'Winner':trainWinner})
trainGames

testRadiant = games["Radiant"][0:96]
testDire = games["Dire"][0:96]
testWinner = games["Winner"][0:96]

testGames = pd.DataFrame(data = {'Radiant':testRadiant,'Dire':testDire,'Winner':testWinner})
testGames

Radiant                 Dire  Winner
0                    OG          Team Liquid     1.0
1           Team Liquid                   OG     0.0
2           Team Liquid                   OG     0.0
3           Team Liquid                   OG     1.0
4               PSG.LGD          Team Liquid     0.0
5           Team Liquid              PSG.LGD     1.0
6           Team Liquid              PSG.LGD     0.0
7           Team Secret          Team Liquid     0.0
8           Team Liquid          Team Secret     1.0
9                    OG              PSG.LGD     1.0
10              PSG.LGD                   OG     0.0
11                   OG              PSG.LGD     0.0
12          Team Secret          Vici Gaming     1.0
13          Vici Gaming          Team Secret     0.0
14          Team Liquid        Evil Geniuses     1.0
15          Team Liquid        Evil Geniuses     1.0
16          Team Secret      Infamous Gaming     1.0
17      Infamous Gaming          Team Secret     0.0
18          Team Liquid  Royal Never Give Up     1.0
19  Royal Never Give Up          Team Liquid     0.0
20                   OG        Evil Geniuses     1.0
21                   OG        Evil Geniuses     1.0
22        Evil Geniuses                   OG     1.0
23          Vici Gaming              PSG.LGD     0.0
24          Vici Gaming              PSG.LGD     0.0
25              Mineski          Team Secret     0.0
26              Mineski          Team Secret     1.0
27              Mineski          Team Secret     0.0
28               Newbee      Infamous Gaming     0.0
29      Infamous Gaming               Newbee     0.0
..                  ...                  ...     ...
66          Vici Gaming        Natus Vincere     1.0
67        Evil Geniuses           Virtus.pro     0.0
68    Ninjas in Pyjamas      Infamous Gaming     1.0
69  Royal Never Give Up               Fnatic     0.0
70           Virtus.pro        Evil Geniuses     0.0
71        Natus Vincere          Vici Gaming     0.0
72      Infamous Gaming    Ninjas in Pyjamas     1.0
73          Team Secret              PSG.LGD     0.0
74          Team Liquid          KEEN GAMING     1.0
75          Team Secret              PSG.LGD     0.0
76               Newbee   Chaos Esports Club     1.0
77              Mineski             Alliance     0.0
78               Fnatic                   OG     0.0
79               Newbee   Chaos Esports Club     1.0
80          KEEN GAMING          Team Liquid     0.0
81             Alliance              Mineski     0.0
82               Fnatic                   OG     0.0
83  Royal Never Give Up        Natus Vincere     1.0
84    Ninjas in Pyjamas          Vici Gaming     1.0
85      Infamous Gaming           Virtus.pro     0.0
86        Natus Vincere  Royal Never Give Up     0.0
87          Vici Gaming    Ninjas in Pyjamas     1.0
88           Virtus.pro      Infamous Gaming     1.0
89         TNC Predator   Chaos Esports Club     0.0
90             Alliance          Team Liquid     1.0
91          KEEN GAMING               Newbee     1.0
92              Mineski          Team Secret     1.0
93          Team Liquid             Alliance     1.0
94         TNC Predator   Chaos Esports Club     1.0
95          Team Secret              Mineski     1.0

[96 rows x 3 columns]

In [53]:
trainTeamsX = designMatrix(trainGames, index_dict)
trainTeams = BTfit(trainTeamsX, trainGames["Winner"], Teamlist,1)

In [54]:
trainTeams

Teams                  Ranks
0                    OG   [17.122370042145498]
1           Team Liquid   [0.7373584888281122]
2               PSG.LGD    [7.316723688483144]
3           Team Secret   [18.030292504239256]
4           Vici Gaming   [3.5950589978717997]
5         Evil Geniuses   [2.8638585375245365]
6   Royal Never Give Up  [0.37709516849111274]
7       Infamous Gaming    [3.786604373998368]
8                Newbee   [3.6188662374789997]
9          TNC Predator   [3.1344166343892623]
10           Virtus.pro   [0.3763778463383115]
11               Fnatic    [2.022545019883788]
12             Alliance   [2.1061589595709957]
13              Mineski   [1.2254729260313995]
14        Natus Vincere   [2.8159458426509274]
15   Chaos Esports Club   [0.1526913691943264]
16          KEEN GAMING   [0.9439563508867802]
17    Ninjas in Pyjamas  [0.10441341726336681]

In [55]:
wins = 0
for i in range(len(testGames["Radiant"])):
    li = trainTeams["Ranks"][index_dict[testGames["Radiant"][i]]][0]
    lj = trainTeams["Ranks"][index_dict[testGames["Dire"][i]]][0]
    result = testGames["Winner"][i]
    pi = li/(li + lj)
    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy1 = wins/len(testGames["Radiant"])
test_accuracy1

54


0.5625

In [56]:
heroes1 = []
heroes2 = []
i = 0
for game in Stats:
    if i == 0:
        i += 1
    else:
        heroes1.append(Stats[i][2])
        heroes2.append(Stats[i][5])
        i += 1   
heroes1new = []
heroes2new = []
for i in heroes1:
    heroes1new.append(i.split("  "))

for i in heroes2:
    heroes2new.append(i.split("  "))

    
trainHeroes1 = heroes1new[97:]
trainHeroes2 = heroes2new[97:]
testHeroes1 = heroes1new[0:96]
testHeroes2 = heroes2new[0:96]

Matchups1 = []
binWins2 = []
for i in trainHeroes1:
    for j in i:
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)
        Matchups1.append(j)


Matchups2 = []
for i in trainHeroes2:
    for j in range(5):
        Matchups2.append(i[0])
        Matchups2.append(i[1])
        Matchups2.append(i[2])
        Matchups2.append(i[3])
        Matchups2.append(i[4])

    
for i in binWins[97:]:
    for j in range(25):
        binWins2.append(i)

d = {'Radiant':Matchups1, 'Dire':Matchups2, 'Winner':binWins2}
trainHeroGames = pd.DataFrame(data = d)


In [57]:
trainHeroes1X = designMatrix(trainHeroGames, hdict)
trainHeroesSkill1 = BTfit(trainHeroes1X, binWins2, heroes,1)
trainHeroesSkill1

Teams                  Ranks
0                  Io    [4.900484512621467]
1                Tiny    [2.440821801348335]
2             Abaddon   [2.2065670082974718]
3           Timbersaw   [1.0041577753569206]
4          Gyrocopter    [3.847958164384253]
5              Rubick   [1.6836511111452768]
6          Tidehunter    [4.119283294357114]
7           Ogre Magi   [2.4071195943612937]
8    Templar Assassin    [4.489170151608479]
9          Juggernaut   [1.0775430857900263]
10      Shadow Shaman   [3.7844935532244066]
11        Lifestealer   [2.6995514679362373]
12             Enigma   [1.2439433969567786]
13               Chen   [5.4296962940319675]
14              Meepo    [1.102644241006787]
15        Elder Titan   [2.6813844827418074]
16      Faceless Void    [1.822516034755861]
17       Shadow Fiend   [2.2425469996260974]
18          Dark Seer   [1.1620474526787943]
19               Sven    [2.191336198448039]
20             Mirana   [3.0397963916238115]
21             Tinker    [2.336376937027574]
22       Shadow Demon   [3.2894267309878154]
23             Magnus   [2.8442072328221264]
24        Wraith King    [2.863082418809693]
25        Bristleback    [7.474756513195233]
26       Earth Spirit    [5.845874834446868]
27            Leshrac   [2.7775355603197367]
28          Alchemist    [2.927852195621253]
29   Legion Commander    [3.661434847914867]
..                ...                    ...
85        Drow Ranger   [0.1813770950602573]
86      Skywrath Mage   [10.262212079478127]
87        Dark Willow   [4.1291237550003315]
88         Naga Siren     [4.69739967190915]
89            Undying    [1.514921094430787]
90            Spectre   [3.3414814450863592]
91              Pudge   [1.1543712246062474]
92             Clinkz   [1.6255467518666633]
93        Bloodseeker   [0.8669256135596369]
94       Chaos Knight   [1.0302065508996447]
95              Viper    [1.970619096103515]
96               Bane   [0.9675614520267634]
97            Slardar    [3.357641310078741]
98             Huskar  [0.44877484133078677]
99      Troll Warlord   [0.7524109726475766]
100        Lone Druid  [0.08077242497861895]
101   Vengeful Spirit   [0.0872715314411337]
102  Treant Protector   [14.869524620339275]
103            Dazzle   [1.1426534509384618]
104         Disruptor  [0.10904282306389751]
105           Phoenix   [0.6029031781504582]
106              Tusk   [2.5130298908401487]
107              Luna   [0.2928076135297569]
108              Doom   [0.4150949731656271]
109             Lycan   [0.2743369897848981]
110    Spirit Breaker   [0.3889714759249518]
111     Night Stalker   [1.5745899291130012]
112     Bounty Hunter   [1.5085940617625275]
113        Venomancer   [0.1789262137583458]
114      Ember Spirit   [0.3942795882112075]

[115 rows x 2 columns]

In [58]:
testTeamskill1 = np.zeros(96)
testTeamskill2 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
testTeamskill1
testTeamskill2

array([30.95377841, 11.54251403, 22.57793948, 14.05554056, 17.71602532,
       10.38075733, 14.27092013, 14.57500262, 13.92327551, 13.45069406,
       12.34938922, 13.31089711, 14.3239216 , 15.8299232 , 15.27983261,
       15.33405596, 13.61628521, 14.74318535, 13.84092   , 15.44523889,
       14.15983638, 14.09711018, 27.63679489, 14.03410149, 11.99563596,
        9.29036558, 13.26061038, 10.85262181, 17.27054744, 18.4838951 ,
       26.1951778 , 17.31340895, 17.3035906 , 13.6554956 , 13.5628265 ,
       15.78644762, 14.53696342, 21.90815979, 36.18768896, 17.40226877,
       12.19159146, 22.2916021 , 11.94763473, 16.51578747, 16.15757757,
       16.03252612, 13.96183416, 17.92182363, 16.34132705, 11.20198802,
       16.8690448 , 30.42969322, 12.62142656, 13.80902445, 14.99531827,
       14.13072069,  9.38322572, 14.72573262,  9.0643379 , 11.15982359,
       11.40686117, 17.51360093, 22.99830176, 11.73460232, 15.54652495,
       14.05098783, 15.28699025, 13.03242674, 11.50008655, 15.33

In [59]:
testTeamwin1 = 0
for i in range(96):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin1 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin1 += 1
test_accuracy2 = testTeamwin1/len(testGames["Radiant"])
test_accuracy2


0.5104166666666666

In [60]:
k = len(hdict.keys())
r = []

r = np.array(trainWinner)
m = len(r)



Ip = np.zeros((m,k))
I = np.zeros((m,k))
l = 0
for i in trainHeroes1:
    for j in i:
        if trainGames["Winner"][97+l] == 1:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l+=1

l = 0
for i in trainHeroes2:
    for j in i:
        if trainGames["Winner"][97+l] == 0:
            Ip[l,hdict[j]] = 1
        I[l,hdict[j]] = 1
    l += 1  


trainHeroesSkill2 = BTfit2(I,Ip,r,k,10,heroes)

[2.79273355e-01 6.44402312e-02 1.98623614e-01 9.31682745e-01
 8.54413568e-01 9.54734735e-01 5.22533482e-02 5.79471681e-01
 4.80496267e-01 2.17089790e-02 3.73620464e-01 4.14091801e-01
 6.03907234e-01 6.71748727e-01 8.38865700e-01 7.79526208e-01
 4.00701044e-01 7.94529231e-01 8.93124310e-01 2.62489691e-01
 9.89197007e-01 8.53307099e-01 7.31477156e-01 3.55565625e-01
 8.83289491e-01 8.67959091e-01 9.55766446e-01 1.07256520e-04
 1.65410419e-02 3.14070057e-01 9.95316175e-01 1.48844223e-01
 1.67377119e-01 7.58572037e-01 6.95296662e-02 7.05473439e-01
 4.69165282e-01 1.01882161e-02 7.74823863e-01 7.94201008e-01
 1.49569452e-01 2.37036318e-02 7.62063771e-01 2.23670180e-01
 2.62174398e-01 4.56869503e-01 2.49926919e-01 5.68283562e-01
 8.46942997e-01 3.78099537e-01 4.32465116e-01 8.32619176e-01
 3.71131936e-01 4.05532719e-02 5.54671486e-01 4.51246243e-01
 7.25300977e-01 3.78450522e-01 8.40662496e-01 4.69314694e-01
 5.62643429e-01 6.61199339e-01 4.62241868e-01 6.23636945e-01
 2.21880631e-01 7.328631

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:62: RuntimeWarning: invalid value encountered in double_scalars


In [61]:
testTeamskill3 = np.zeros(96)
testTeamskill4 = np.zeros(96)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
testTeamskill3
testTeamskill4

testTeamwin2 = 0
for i in range(96):
    prob = testTeamskill3[i]/(testTeamskill3[i]+testTeamskill4[i])
    result = testGames["Winner"][i]
    if prob < 0.5 and result ==0:
        testTeamwin2 += 1
    if prob >= 0.5 and result ==1:
        testTeamwin2 += 1
test_accuracy3 = testTeamwin2/len(testGames["Radiant"])
test_accuracy3

0.5520833333333334

In [62]:
wincounts = np.zeros(len(Teamlist))
index = 97
for i in trainGames["Radiant"]:
    if trainGames["Winner"][index] == 1:
        wincounts[index_dict[i]] += 1
    index+=1

index = 97
for i in trainGames["Dire"]:
    if trainGames["Winner"][index] == 0:
        wincounts[index_dict[i]] += 1
    index+=1
    
wincounts

array([11.,  3., 10.,  9.,  7.,  6.,  3.,  5.,  5.,  6.,  3.,  5.,  5.,
        5.,  7.,  1.,  4.,  1.])

In [63]:
trainTeamskill1 = np.zeros(m)
trainTeamskill2 = np.zeros(m)

index = 0
for i in trainHeroes1:
    for j in i:
        trainTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in trainHeroes2:
    for j in i:
        trainTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

trainTeamskill3 = np.zeros(m)
trainTeamskill4 = np.zeros(m)

index = 0
l = 97
for i in trainHeroes1:
    for j in i:
        if trainGames["Winner"][l] == 1:
            trainTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        trainTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    l += 1
    
index = 0
l = 97
for i in trainHeroes2:
    for j in i:
        if trainGames["Winner"][l] == 0:
            trainTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        trainTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    l += 1
    
trainTeamwin1 = np.zeros(m)
for i in range(m):
    prob = trainTeamskill1[i]/(trainTeamskill1[i] + trainTeamskill2[i])
    if prob >= 0.5:
        trainTeamwin1[i] = 1    

trainTeamwin2 = np.zeros(m)
for i in range(m):
    if (trainTeamskill3[i]/trainTeamskill4[i]) > 0.5:
        trainTeamwin2[i] = 1

trainGames["Team Winner"] =trainTeamwin1
trainGames["Team Winner 2"] = trainTeamwin2

k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97

for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')

data = {"Teams":Teamlist, "Ranks":np.exp(res.x[:-1]),"Draft Advantage 1":np.exp(res.x[-1])}


Teamhg3 = pd.DataFrame(data)


k = len(index_dict.keys())
aij = np.zeros((k,k))
bij = np.zeros((k,k))
l = 97
for i in trainGames["Radiant"]:
    j = trainGames["Dire"][l]
    if trainGames["Team Winner 2"][l] == 1:
        aij[index_dict[i]][index_dict[j]]+=1
    else:
        bij[index_dict[i]][index_dict[j]]+=1
    l+=1
nij = aij + bij
c = sum(trainGames["Team Winner 2"])

np.random.seed(12345)
x0 = np.random.rand(k+1)
x0[-1] = 1
res = minimize(BTloglik, x0, method = 'nelder-mead')
data = {"Teams":Teamlist, "Ranks":res.x[:-1]/np.min(res.x[:-1]),"Draft Advantage 2":res.x[-1]}

Teamhg4 = pd.DataFrame(data)


[25.15272366 15.34087505 13.22156716 13.55183063 19.36246664 19.80758143
 25.71109849 20.72969973 22.26137238 20.73598411 22.24230313 25.65977395
 10.41307894 11.9819762  15.0581256  20.78144511 23.23586702 24.2336808 ]
[25.94289734 15.38735586 13.26804797 13.59831144 19.40894745 19.85406223
 25.7575793  20.77618053 22.30785318 20.78246492 22.28878393 25.70625476
 10.45955975 12.02845701 15.1046064  20.82792591 23.28234782 24.2801616 ]
[25.16854244 15.60979427 13.23738594 13.56764941 19.37828542 19.8234002
 25.72691727 20.74551851 22.27719116 20.75180289 22.2581219  25.67559273
 10.42889772 11.99779498 15.07394438 20.79726388 23.2516858  24.24949958]
[25.1619196  15.35007099 13.37789815 13.56102658 19.37166258 19.81677737
 25.72029443 20.73889567 22.27056832 20.74518005 22.25149907 25.6689699
 10.42227489 11.99117215 15.06732154 20.79064105 23.24506296 24.24287674]
[25.16295168 15.35110307 13.23179518 13.72570687 19.37269466 19.81780944
 25.72132651 20.73992774 22.27160039 20.74621213 

[25.27645007 15.34516394 13.24431759 13.58091553 19.47080532 19.57530617
 24.30115302 21.04483236 21.84766378 20.70352468 22.03406201 25.44048536
 10.32883053 11.93707706 15.10264722 20.50080247 23.0605696  23.72332356]
[25.26099414 15.33658834 13.24189851 13.57850907 19.46522358 20.11501579
 24.20758835 20.60872129 21.78123725 20.68035796 22.02524706 25.38782638
 10.32069748 11.92998086 15.09887858 20.48618232 23.05253669 23.7020016 ]
[25.26645789 15.35171074 13.2642731  13.60082867 19.48281797 19.74316254
 24.1354516  20.62536563 21.73092574 20.67821479 22.04243457 26.29193633
 10.33733811 11.94744084 15.11937703 20.49714164 23.07030601 23.70738998]
[25.14686538 15.31061276 13.24513454 13.57930971 19.4157778  19.5506223
 25.21207848 20.39870216 21.57766896 20.58237386 21.72430448 25.37517666
 10.33243356 11.93227526 15.08547991 20.19011415 22.75036926 23.46755909]
[25.18884677 15.32375912 13.25893394 13.5944395  19.44930885 19.69838956
 24.19555179 20.57195169 21.75294841 21.23348533

  8.36306091 10.46471317 14.34947587 14.19368005 16.38040344 10.48596298]
[20.74115129 13.11301012 13.41385952 12.98714158 18.32494709 11.00590488
 12.91801366 11.54117983 10.12520114 16.10263497 13.46243191 18.13907783
  8.13074443  9.95298353 13.26636748 12.24888545 13.59541082  8.01930896]
[25.37421236 14.86598698 15.12692819 14.39720637 21.7168954  12.43371209
 14.89881346 13.35836324 11.37222209 19.23457302 16.21476864 21.92894535
  8.32223722 10.65902327 14.88769519 14.89723793 16.91061156 10.46134753]
[23.89186112 14.40707894 14.6855636  14.04398049 20.88379148 12.0446786
 14.04029501 13.57100558 12.34298942 18.28736046 15.34665306 20.75882527
  8.29217662 10.49750117 14.42109923 14.64303906 14.67408256 10.04945701]
[23.54610675 14.29556357 14.92784486 14.29358688 20.79953909 10.85475864
 17.01848752 11.6546238  11.18898344 17.61539638 13.86387799 20.21103667
  8.09045015 10.34833565 14.4003239  13.14427809 13.91380073  8.50256448]
[23.91191009 14.33492692 15.15369815 14.3480493

C:\Users\Rowan\Anaconda3\lib\site-packages\ipykernel_launcher.py:23: RuntimeWarning: invalid value encountered in log



[23.75496875 14.69640637 16.06813665 15.01656898 19.91452389 10.63311538
 14.1260828  12.37771641 16.49537893 18.46002643 15.06294646 22.18866345
  7.94453219 10.55229398 14.85908006 12.93940915 13.78987054  9.70146658]
[24.69277974 14.76277057 15.36628164 14.60522673 21.17575263 11.63877976
 13.10677222 13.4657285  14.44427271 18.70801077 15.42823894 21.78694647
  8.13308064 10.58438625 14.78715926 14.65862712 14.27252067 10.13589181]
[24.91099381 14.82712151 15.64077962 14.8305175  21.05093736 11.80142772
 13.75040504 13.06410666 14.66353729 18.65671235 15.33178561 22.27429694
  8.08002302 10.58488708 14.94681189 13.74403446 15.0250018  10.11545808]
[23.26344242 14.14420881 15.06567993 14.3205042  20.08316763 10.55515319
 12.71176638 11.69746492 13.11169264 17.39449624 13.89958578 20.18278935
  7.88255033 10.24384896 14.32505051 12.7196264  13.17049082  8.13986701]
[24.88205969 14.8513472  15.68865488 14.88070499 20.6252552  11.44003385
 13.18571762 12.76269272 15.8929448  18.665958

...

[15.4475108  11.29475712 11.3002197  17.45096447 16.58692893 10.04731619
  7.9381188  11.19912003 10.85843089 11.27633343  7.70722412 13.52873794
  5.84473839 14.60764845 11.7572767   5.67036771  7.91429129  6.18149174]
[15.74085085 11.36897102 11.18476506 17.10544997 16.46707908 10.21366182
  7.82103559 11.05883684 10.81358534 11.44291625  7.85157634 13.50057192
  5.86682991 14.776919   11.87944256  5.68356849  7.86786878  6.14752411]
[15.47752027 11.27878076 11.25782393 17.28446756 16.57067782 10.22540484
  7.80296209 11.11114769 10.68185084 11.67409601  7.76929416 13.53639479
  5.85207542 14.64896702 11.80021934  5.66655076  7.88415696  6.18129109]
[15.52843173 11.33116768 11.16320133 17.09218264 16.36598988 10.00372574
  7.92809281 11.13649223 10.91760358 11.27834486  7.78096683 13.23418418
  5.8585608  14.66356746 11.78077068  5.69320449  7.91512402  6.18155671]
[15.68755096 11.38464446 11.33497663 17.39780997 16.70208597 10.20223046
  8.00294701 11.18847791 11.03352216 11.2846318

[15.61300838 11.25458056 11.11776315 17.28306545 16.32687463  9.92571677
  7.87078962 11.1240317  10.6781124  11.28860227  7.7605012  13.58698253
  5.8449862  14.83880108 11.86833201  5.6983675   7.92948767  6.1921003 ]
[15.6496503  11.23754241 11.14334396 17.35967054 16.36178799  9.80973351
  7.91453159 11.11688697 10.76714019 11.25452387  7.74157512 13.49291024
  5.84070746 14.8041848  11.84834862  5.68943614  7.88960194  6.21792753]
[15.77366424 11.2895701  11.16716304 17.37102318 16.47833857  9.91968429
  7.93117134 11.14315082 10.81620836 11.32095328  7.78613636 13.62526334
  5.85599111 14.84228329 11.93093303  5.69471132  7.93437903  6.23896534]
[15.85075093 11.30829532 11.16899751 17.4054802  16.54791321  9.93048259
  7.95858067 11.13665946 10.8705198  11.30673191  7.77643363 13.70514939
  5.86115639 14.88885863 12.00453857  5.69447363  7.94034338  6.24932129]
[15.73835986 11.2535129  11.12568262 17.27876684 16.34723483  9.93823391
  7.89998806 11.11430131 10.71955652 11.4515980

  5.84670661 14.92207011 11.97591506  5.6927048   7.96209743  6.20467554]
[15.81068834 11.20994286 11.12762728 17.43649886 16.34498684  9.89888881
  7.87568787 11.11078682 10.63430303 11.41250088  7.77781412 13.65013089
  5.84422031 14.86465571 11.87794439  5.68616328  7.93367435  6.22985697]
[16.0210425  11.33608585 11.13436391 17.3894599  16.60789916  9.80803694
  7.90201333 11.20835372 10.89152134 11.41269801  7.85453291 13.83322705
  5.87453624 14.96717511 12.07471133  5.70815353  7.99611387  6.23528731]
[16.02138278 11.29713726 11.16752229 17.47259735 16.58066066  9.78486254
  7.90959606 11.19237713 10.87667346 11.43227476  7.84436972 13.73025986
  5.86655892 14.89253066 11.98764523  5.70739106  7.96629569  6.26150801]
[16.08529101 11.29814507 11.2011085  17.53751291 16.6341912   9.73524843
  7.92475098 11.20662786 10.94030777 11.45093997  7.85786345 13.68749124
  5.86810198 14.85236474 11.96417072  5.71329024  7.95674001  6.2881057 ]
[16.06617878 11.29402085 11.14373465 17.533947

[16.24124496 11.09049167 11.14404375 18.03801343 17.03326221  9.80728521
  8.07279997 11.14057095 10.87775692 11.56763977  7.85255046 13.73379063
  5.88691582 14.48593528 12.43366029  5.76100033  8.04170181  6.21617076]
[16.40761789 10.96393087 11.09990858 18.23643256 17.12394723  9.78828156
  8.09136784 11.06692395 10.73925818 11.77174178  7.88457738 13.92579738
  5.89256496 14.44467219 12.63371571  5.7566621   8.03780138  6.23050357]
[16.53954382 11.13851394 11.17689298 18.18036697 17.48102124 10.0138484
  8.1353477  11.20526695 10.92634543 11.85178703  8.03051545 14.1306797
  5.93081918 14.48831662 12.83912047  5.77167618  8.16175296  6.26878217]
[16.39326329 11.04262177 11.01516079 17.94529593 16.95279163  9.93144218
  8.11025931 10.97191475 10.84889273 11.6305131   7.8237972  13.87035128
  5.90054918 14.58869979 12.66177229  5.74992017  8.03965396  6.25452469]
[16.41177227 11.10181411 11.11886436 18.04227233 17.23487329  9.90419103
  8.08935078 11.14606971 10.90145107 11.81025783 

  5.88786922 14.2163024  12.25854991  5.84335053  8.08292536  6.18543206]
[16.19428238 10.93240265 11.03181343 17.95608326 16.80142516  9.90178658
  8.01375104 10.95904589 10.69524556 11.71308231  7.83525845 13.74202359
  5.89199231 14.29671333 12.44335818  5.78093504  8.01184545  6.22662249]
[16.5323373  10.94356802 11.06450991 18.17087204 16.98227645 10.03697532
  8.01559743 10.96653957 10.65180881 11.67119251  8.0082511  14.05536466
  5.91395766 14.26024979 12.64192741  5.80880847  8.06229988  6.24460306]
[16.22009309 10.84204193 11.06954453 18.15036123 16.6976014   9.89109336
  7.99480531 10.98711283 10.56160848 11.65423932  7.88766429 13.83870402
  5.88754183 14.11858303 12.32075285  5.78353447  8.05033194  6.27398458]
[16.19505217 10.76526813 11.09938418 18.28651971 16.65026877  9.8817677
  8.00082229 10.98322132 10.51301425 11.67185808  7.87287396 13.83250601
  5.88247722 13.97497419 12.23709482  5.76649841  8.06278444  6.32836179]
[16.29622412 11.07793892 11.10466394 18.0012127

In [64]:
Teamhg4

Teams      Ranks  Draft Advantage 2
0                    OG  16.105615            1.26173
1           Team Liquid   8.212330            1.26173
2               PSG.LGD   8.453914            1.26173
3           Team Secret  18.947449            1.26173
4           Vici Gaming  16.885495            1.26173
5         Evil Geniuses   6.914868            1.26173
6   Royal Never Give Up   4.125893            1.26173
7       Infamous Gaming   8.459233            1.26173
8                Newbee   8.099027            1.26173
9          TNC Predator   9.355769            1.26173
10           Virtus.pro   4.007160            1.26173
11               Fnatic  12.720087            1.26173
12             Alliance   1.138338            1.26173
13              Mineski  12.688821            1.26173
14        Natus Vincere  10.819861            1.26173
15   Chaos Esports Club   1.000000            1.26173
16          KEEN GAMING   4.421653            1.26173
17    Ninjas in Pyjamas   1.698976            1.26173

In [65]:
testTeamskill1 = np.zeros(m)
testTeamskill2 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        testTeamskill1[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        testTeamskill2[index] += trainHeroesSkill1["Ranks"][hdict[j]][0]
    index += 1

testTeamskill3 = np.zeros(m)
testTeamskill4 = np.zeros(m)

index = 0
for i in testHeroes1:
    for j in i:
        if testGames["Winner"][index] == 1:
            testTeamskill3[index] += trainHeroesSkill2["Ranks"][hdict[j]]
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
index = 0

for i in testHeroes2:
    for j in i:
        if testGames["Winner"][index]==0:
            testTeamskill3[index]+= trainHeroesSkill2["Ranks"][hdict[j]]
        testTeamskill4[index] += trainHeroesSkill2["Ranks"][hdict[j]]
    index += 1
    
testTeamwin1 = np.zeros(m)
for i in range(m):
    prob = testTeamskill1[i]/(testTeamskill1[i]+testTeamskill2[i])
    if prob >= 0.5:
        testTeamwin1[i] = 1    

testTeamwin2 = np.zeros(m)
for i in range(m):
    if testTeamskill3[i]/(testTeamskill4[i]) > 0.5:
        testTeamwin2[i] = testGames["Winner"][i]

testGames["Team Winner"] = testTeamwin1
testGames["Team Winner 2"] = testTeamwin2


wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg3["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg3["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner"][i]== 1:
        """Radiant is home team"""
        pi = Teamhg3["Draft Advantage 1"][0]*li/(Teamhg3["Draft Advantage 1"][0]*li + lj)
    elif 0 == testGames["Team Winner"][i]:
        """Dire is home team"""
        pi = li/(Teamhg3["Draft Advantage 1"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy4 = wins/len(testGames["Radiant"])
test_accuracy4

48


0.5

In [66]:
wins = 0
for i in range(len(testGames["Radiant"])-1):
    li = Teamhg4["Ranks"][index_dict[testGames["Radiant"][i]]]
    lj = Teamhg4["Ranks"][index_dict[testGames["Dire"][i]]]
    result = testGames["Winner"][i]
    if testGames["Team Winner 2"][i]== 1:
        """Radiant is winning team"""
        pi = Teamhg4["Draft Advantage 2"][0]*li/(Teamhg4["Draft Advantage 2"][0]*li + lj)
    elif 0 == testGames["Team Winner 2"][i]:
        """Dire is winning team"""
        pi = li/(Teamhg4["Draft Advantage 2"][0]*lj + li)        

    if pi >= 0.5 and result ==1:
        wins +=1
    elif pi < 0.5 and result ==0:
        wins +=1
print(wins)
test_accuracy5 = wins/len(testGames["Radiant"])
test_accuracy5

58


0.6041666666666666

In [67]:
test2.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [68]:
testTeamwin2

array([0., 0., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 1.,
       0., 1., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 1., 0.,
       0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 1., 0.,
       1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 0., 1., 0., 0., 0., 1., 1.,
       0., 0., 1., 1., 0., 1., 0., 1., 1., 0., 1.])

In [69]:
test_accuracy1

0.5625

In [70]:
test4.sort_values(by=['Ranks'], inplace=True, ascending=False)

#### 

In [71]:
test4[:18]

Teams                 Ranks
75      Winter Wyvern  [16.385541900741657]
18          Dark Seer   [8.353638378924396]
37         Windranger   [7.139688993064939]
21             Tinker   [6.998854558643562]
0                  Io   [6.937033130253285]
102  Treant Protector   [6.933359386566875]
111     Night Stalker   [6.531994105786769]
13               Chen  [5.4529544290316725]
14              Meepo   [4.968784289914939]
78        Monkey King   [4.674884012367447]
8    Templar Assassin   [4.614054068024755]
97            Slardar   [4.317210883329904]
2             Abaddon  [3.9119549503711766]
16      Faceless Void  [3.7503109627488675]
40             Medusa  [3.6866477255946517]
6          Tidehunter   [3.597177531447213]
4          Gyrocopter  [3.4316576574301987]
86      Skywrath Mage   [3.415373675676189]

In [72]:
Teamhg4

Teams      Ranks  Draft Advantage 2
0                    OG  16.105615            1.26173
1           Team Liquid   8.212330            1.26173
2               PSG.LGD   8.453914            1.26173
3           Team Secret  18.947449            1.26173
4           Vici Gaming  16.885495            1.26173
5         Evil Geniuses   6.914868            1.26173
6   Royal Never Give Up   4.125893            1.26173
7       Infamous Gaming   8.459233            1.26173
8                Newbee   8.099027            1.26173
9          TNC Predator   9.355769            1.26173
10           Virtus.pro   4.007160            1.26173
11               Fnatic  12.720087            1.26173
12             Alliance   1.138338            1.26173
13              Mineski  12.688821            1.26173
14        Natus Vincere  10.819861            1.26173
15   Chaos Esports Club   1.000000            1.26173
16          KEEN GAMING   4.421653            1.26173
17    Ninjas in Pyjamas   1.698976            1.26173

In [73]:
test5.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [74]:
test5[:18]

Heroes     Ranks
22        Shadow Demon  0.040212
11         Lifestealer  0.030500
7            Ogre Magi  0.025347
15         Elder Titan  0.024969
48   Centaur Warrunner  0.021864
69          Grimstroke  0.020662
6           Tidehunter  0.019730
19                Sven  0.019481
23              Magnus  0.019041
51         Earthshaker  0.018551
72         Broodmother  0.017598
50             Invoker  0.017266
43            Silencer  0.016167
105            Phoenix  0.015821
16       Faceless Void  0.015642
84   Outworld Devourer  0.015459
100         Lone Druid  0.015000
93         Bloodseeker  0.014703

In [75]:
test_accuracy3

0.5520833333333334

In [93]:
Teamhg3

Teams     Ranks  Draft Advantage 1
0                    OG  1.695505            2.09067
1           Team Liquid  1.210755            2.09067
2               PSG.LGD  2.044374            2.09067
3           Team Secret  1.496713            2.09067
4           Vici Gaming  1.436743            2.09067
5         Evil Geniuses  1.235595            2.09067
6   Royal Never Give Up  1.157072            2.09067
7       Infamous Gaming  1.276517            2.09067
8                Newbee  1.322080            2.09067
9          TNC Predator  1.464321            2.09067
10           Virtus.pro  1.142474            2.09067
11               Fnatic  1.334261            2.09067
12             Alliance  1.056505            2.09067
13              Mineski  1.137433            2.09067
14        Natus Vincere  1.509645            2.09067
15   Chaos Esports Club  1.041078            2.09067
16          KEEN GAMING  1.223202            2.09067
17    Ninjas in Pyjamas  1.057950            2.09067

In [77]:
Teamhg3

Teams     Ranks  Draft Advantage 1
0                    OG  1.695505            2.09067
1           Team Liquid  1.210755            2.09067
2               PSG.LGD  2.044374            2.09067
3           Team Secret  1.496713            2.09067
4           Vici Gaming  1.436743            2.09067
5         Evil Geniuses  1.235595            2.09067
6   Royal Never Give Up  1.157072            2.09067
7       Infamous Gaming  1.276517            2.09067
8                Newbee  1.322080            2.09067
9          TNC Predator  1.464321            2.09067
10           Virtus.pro  1.142474            2.09067
11               Fnatic  1.334261            2.09067
12             Alliance  1.056505            2.09067
13              Mineski  1.137433            2.09067
14        Natus Vincere  1.509645            2.09067
15   Chaos Esports Club  1.041078            2.09067
16          KEEN GAMING  1.223202            2.09067
17    Ninjas in Pyjamas  1.057950            2.09067

In [78]:
test_accuracy4

0.5

In [79]:
test_accuracy5

0.6041666666666666

In [80]:
teamhg3

NameError: name 'teamhg3' is not defined

In [ ]:
Teamhg3

In [ ]:
testGames

In [ ]:
testHeroes1

In [ ]:
Teamhg3

Need to do some testing against coin-flip

In [ ]:
cointoss = []
for i in range(10000):
    wins = 0
    for i in testGames["Winner"]:
        if i == random.randint(0,1):
            wins+=1
    cointoss.append(wins)

In [ ]:
np.mean(cointoss)/len(testGames["Winner"])

In [ ]:
sum(binWins)/len(binWins)

In [ ]:
teamhg

In [ ]:
cointoss

In [ ]:
test_accuracy1

In [81]:
test_accuracy2

0.5104166666666666

In [ ]:
test_accuracy3

In [ ]:
test_accuracy4

In [ ]:
test_accuracy5

In [ ]:
np.mean(cointoss)/len(testGames["Winner"])

In [ ]:
test2.sort_values(by=['Ranks'], inplace=True, ascending=False)

In [ ]:
test2

In [85]:
test4[:18]

Teams                 Ranks
75      Winter Wyvern  [16.385541900741657]
18          Dark Seer   [8.353638378924396]
37         Windranger   [7.139688993064939]
21             Tinker   [6.998854558643562]
0                  Io   [6.937033130253285]
102  Treant Protector   [6.933359386566875]
111     Night Stalker   [6.531994105786769]
13               Chen  [5.4529544290316725]
14              Meepo   [4.968784289914939]
78        Monkey King   [4.674884012367447]
8    Templar Assassin   [4.614054068024755]
97            Slardar   [4.317210883329904]
2             Abaddon  [3.9119549503711766]
16      Faceless Void  [3.7503109627488675]
40             Medusa  [3.6866477255946517]
6          Tidehunter   [3.597177531447213]
4          Gyrocopter  [3.4316576574301987]
86      Skywrath Mage   [3.415373675676189]

In [87]:
test5[:18]

Heroes     Ranks
22        Shadow Demon  0.040212
11         Lifestealer  0.030500
7            Ogre Magi  0.025347
15         Elder Titan  0.024969
48   Centaur Warrunner  0.021864
69          Grimstroke  0.020662
6           Tidehunter  0.019730
19                Sven  0.019481
23              Magnus  0.019041
51         Earthshaker  0.018551
72         Broodmother  0.017598
50             Invoker  0.017266
43            Silencer  0.016167
105            Phoenix  0.015821
16       Faceless Void  0.015642
84   Outworld Devourer  0.015459
100         Lone Druid  0.015000
93         Bloodseeker  0.014703

In [88]:
test_accuracy2

0.5104166666666666

In [89]:
test_accuracy3

0.5520833333333334

In [95]:
test_accuracy4

0.5